In [1]:
!pip install selenium
!pip install beautifulsoup4
!pip install webdriver-manager

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.7/9.7 MB 198.9 kB/s eta 0:00:00a 0:00:02
  Attempting uninstall: attrs
    Found existing installation: attrs 23.1.0
    Uninstalling attrs-23.1.0:
      Successfully uninstalled attrs-23.1.0


In [33]:
from selenium import webdriver
from selenium.webdriver.common.by import By
import time

# Example: Driver initialization
driver = webdriver.Chrome()
driver.get("https://www.booking.com/searchresults.html?ss=Paris&nflt=SustainablePropertyLevelFilter%3D4")

time.sleep(5)  # Let the page load or use explicit wait
try:
    cookie_btn = wait.until(EC.element_to_be_clickable(
            (By.CSS_SELECTOR, "button#onetrust-reject-all-handler")
        ))
    cookie_btn.click()
    print("Accepted cookies.")
except:
    print("No cookie popup found.")
# Locate all hotel cards
hotel_cards = driver.find_elements(By.CSS_SELECTOR, "div[data-testid='property-card']")

# Container for the hotel data
results = []

for card in hotel_cards:
    hotel_info = {}

    # 1. Hotel Name
    # There's typically a <div data-testid="title"> for the name
    try:
        name_div = card.find_element(By.CSS_SELECTOR, "div[data-testid='title']")
        hotel_info["Name"] = name_div.text.strip()
    except:
        hotel_info["Name"] = "N/A"

    # 2. Address
    # A <span data-testid="address">
    try:
        address_span = card.find_element(By.CSS_SELECTOR, "span[data-testid='address']")
        hotel_info["Address"] = address_span.text.strip()
    except:
        hotel_info["Address"] = "N/A"

    # 3. Short Description
    # Usually in a <div class="abf093bdfe"> or check for data-testid
    try:
        description_div = card.find_element(By.CSS_SELECTOR, "div.abf093bdfe")
        hotel_info["Description"] = description_div.text.strip()
    except:
        hotel_info["Description"] = "N/A"

    # 4. Rating & Reviews
    # The rating block is in <div data-testid="review-score">
    try:
        score_div = card.find_element(By.CSS_SELECTOR, "div[data-testid='review-score']")
        # Numeric score in the smaller sub-element
        numeric_score = score_div.find_element(By.CLASS_NAME, "ac4a7896c7").text.strip()
        hotel_info["Rating"] = numeric_score
        # Overall text rating, e.g., "Very Good"
        text_rating_elem = score_div.find_element(By.CLASS_NAME, "a3b8729ab1.e6208ee469.cb2cbb3ccb")
        hotel_info["RatingText"] = text_rating_elem.text.strip()
        # e.g., "1,398 reviews"
        reviews_elem = score_div.find_element(By.CSS_SELECTOR, "div.abf093bdfe.f45d8e4c32.d935416c47")
        hotel_info["NumReviews"] = reviews_elem.text.strip()
    except:
        hotel_info["Rating"] = "N/A"
        hotel_info["RatingText"] = "N/A"
        hotel_info["NumReviews"] = "N/A"

    # 5. Hotel Link
    # Typically found in <a data-testid="title-link">
    try:
        title_link = card.find_element(By.CSS_SELECTOR, "a[data-testid='title-link']")
        hotel_info["HotelLink"] = title_link.get_attribute("href")
    except:
        hotel_info["HotelLink"] = "N/A"

    # Add the collected data to results
    results.append(hotel_info)

# Print or store results
for idx, h in enumerate(results, 1):
    print(f"\nHotel {idx}:")
    for k, v in h.items():
        print(f"{k}: {v}")

# Optionally, you might save results into a CSV or JSON later



Hotel 1:
Name: NH Paris Gare de l'Est
Address: 10e arr., Paris
Description: 10e arr., ParisIndiquer sur la carte2,2 km du centreProche du métro
Rating: Avec une note de 8,1
RatingText: Très bien
NumReviews: 1 398 expériences vécues
HotelLink: https://www.booking.com/hotel/fr/mercure-terminus-est.fr.html?aid=304142&label=gen173nr-1FCAQoggJCDHNlYXJjaF9wYXJpc0gzWARoTYgBAZgBDbgBB8gBDNgBAegBAfgBA4gCAagCA7gCgYamuwbAAgHSAiQyM2JmZjMzMy0yMGE4LTQzYTUtYTI3OC0yOWJiN2Y5NDA4MjXYAgXgAgE&ucfs=1&arphpl=1&group_adults=2&req_adults=2&no_rooms=1&group_children=0&req_children=0&hpos=1&hapos=1&sr_order=popularity&nflt=SustainablePropertyLevelFilter%3D4&srpvid=79a16d80adc9016c&srepoch=1734968069&from_sustainable_property_sr=1&from=searchresults

Hotel 2:
Name: Citadines Austerlitz Paris
Address: 13e arr., Paris
Description: 13e arr., ParisIndiquer sur la carte2,5 km du centreProche du métro
Rating: Avec une note de 8,2
RatingText: Très bien
NumReviews: 1 971 expériences vécues
HotelLink: https://www.booking

First Try

In [34]:
import time
import csv
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException, ElementClickInterceptedException
from webdriver_manager.chrome import ChromeDriverManager

def scrape_sustainable_hotels_in_paris():
    # 1. Initialize WebDriver
    driver = webdriver.Chrome()
    driver.maximize_window()

    try:
        # 2. Navigate to Booking.com with the Sustainability Filter in the URL
        #    This avoids having to click the checkbox ourselves.
        url = (
            "https://www.booking.com/searchresults.html"
            "?ss=Paris"
            "&nflt=SustainablePropertyLevelFilter%3D4"
        )
        driver.get(url)
        time.sleep(5)  # Let page load or use explicit wait if needed

        # 3. A container to hold all hotel data
        all_hotels_data = []

        while True:
            # 4. Extract hotel cards on the current page
            hotel_cards = driver.find_elements(By.CSS_SELECTOR, "div[data-testid='property-card']")
            print(f"Found {len(hotel_cards)} hotels on this page.")

            # 5. Parse each hotel card
            for card in hotel_cards:
                hotel_info = {}

                # Hotel Name
                try:
                    name_div = card.find_element(By.CSS_SELECTOR, "div[data-testid='title']")
                    hotel_info["Name"] = name_div.text.strip()
                except:
                    hotel_info["Name"] = "N/A"

                # Address
                try:
                    address_span = card.find_element(By.CSS_SELECTOR, "span[data-testid='address']")
                    hotel_info["Address"] = address_span.text.strip()
                except:
                    hotel_info["Address"] = "N/A"

                # Short Description
                # Typically in a <div class="abf093bdfe">, but can vary
                try:
                    desc_div = card.find_element(By.CSS_SELECTOR, "div.abf093bdfe")
                    hotel_info["Description"] = desc_div.text.strip()
                except:
                    hotel_info["Description"] = "N/A"

                # Rating & Reviews
                try:
                    score_div = card.find_element(By.CSS_SELECTOR, "div[data-testid='review-score']")
                    # Numeric rating
                    numeric_score = score_div.find_element(By.CLASS_NAME, "ac4a7896c7").text.strip()
                    hotel_info["Rating"] = numeric_score
                    # Rating text (e.g., "Very Good")
                    text_rating_elem = score_div.find_element(By.CLASS_NAME, "a3b8729ab1.e6208ee469.cb2cbb3ccb")
                    hotel_info["RatingText"] = text_rating_elem.text.strip()
                    # Number of reviews
                    reviews_elem = score_div.find_element(By.CSS_SELECTOR, "div.abf093bdfe.f45d8e4c32.d935416c47")
                    hotel_info["NumReviews"] = reviews_elem.text.strip()
                except:
                    hotel_info["Rating"] = "N/A"
                    hotel_info["RatingText"] = "N/A"
                    hotel_info["NumReviews"] = "N/A"

                # Hotel Link
                try:
                    title_link = card.find_element(By.CSS_SELECTOR, "a[data-testid='title-link']")
                    hotel_info["HotelLink"] = title_link.get_attribute("href")
                except:
                    hotel_info["HotelLink"] = "N/A"

                all_hotels_data.append(hotel_info)

            # 6. Try clicking “Afficher plus de résultats” to load more hotels
            try:
                # Button CSS may vary; check the HTML. Provided class:
                # <button type="button" class="a83ed08757 c21c56c305 bf0537ecb5 f671049264 af7297d90d c0e0affd09">
                show_more_button = driver.find_element(
                    By.CSS_SELECTOR,
                    "button.a83ed08757.c21c56c305.bf0537ecb5.f671049264.af7297d90d.c0e0affd09"
                )
                # Scroll into view if needed
                driver.execute_script("arguments[0].scrollIntoView(true);", show_more_button)
                time.sleep(2)

                show_more_button.click()
                print("Clicked 'Afficher plus de résultats' to load more hotels.")
                time.sleep(5)  # Wait for new results to load
            except (NoSuchElementException, ElementClickInterceptedException):
                print("No more 'Show more results' button found. We've likely reached the last page.")
                break

        # 7. Save to CSV
        csv_filename = "sustainable_hotels_paris.csv"
        with open(csv_filename, "w", newline="", encoding="utf-8") as csvfile:
            fieldnames = ["Name", "Address", "Description", "Rating", "RatingText", "NumReviews", "HotelLink"]
            writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
            writer.writeheader()
            for hotel in all_hotels_data:
                writer.writerow(hotel)

        print(f"Scraped {len(all_hotels_data)} total hotels. Data saved to '{csv_filename}'.")

    finally:
        driver.quit()


if __name__ == "__main__":
    scrape_sustainable_hotels_in_paris()


Found 25 hotels on this page.
No more 'Show more results' button found. We've likely reached the last page.
Scraped 25 total hotels. Data saved to 'sustainable_hotels_paris.csv'.


Second Try (Adding scrolling + Clicking on "load more" button in order to load all the hotels)

In [38]:
import time
import csv
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException, ElementClickInterceptedException
from webdriver_manager.chrome import ChromeDriverManager

def scrape_sustainable_hotels_in_paris():
    driver = webdriver.Chrome()
    driver.maximize_window()

    # This URL includes the Sustainability filter parameter
    base_url = (
        "https://www.booking.com/searchresults.html"
        "?ss=Paris"
        "&nflt=SustainablePropertyLevelFilter%3D4"
    )

    try:
        driver.get(base_url)
        time.sleep(3)
        try:
            cookie_btn = wait.until(EC.element_to_be_clickable(
                (By.CSS_SELECTOR, "button#onetrust-reject-all-handler")
            ))
            cookie_btn.click()
            print("Rejected cookies.")
        except:
            print("No cookie popup found.")

        # List for storing all extracted data
        all_hotels_data = []
        prev_total_hotels_count = 0

        # In some cases, you might keep a "page" or "iteration" counter 
        # to avoid infinite loops if something goes wrong:
        max_iterations = 20

        for _ in range(max_iterations):
            # --- 1) INFINITE SCROLL ATTEMPT ---

            # We'll do incremental scrolling. Track how many hotels we had 
            # before scrolling to see if new ones loaded.
            hotel_cards = driver.find_elements(By.CSS_SELECTOR, "div[data-testid='property-card']")
            initial_count = len(hotel_cards)

            # Scroll in increments (adjust as needed)
            for i in range(20):  # 3 small scroll steps
                driver.execute_script("window.scrollBy(0, 2000);")
                time.sleep(2)

            # Check if new hotels loaded
            hotel_cards = driver.find_elements(By.CSS_SELECTOR, "div[data-testid='property-card']")
            after_scroll_count = len(hotel_cards)
            print(f"Hotel count before scroll: {initial_count}, after scroll: {after_scroll_count}")

            # If the count didn’t increase, infinite scroll has likely ended
            if after_scroll_count == initial_count:
                print("No new hotels loaded by scrolling. Let's try the 'Afficher plus de résultats' button.")
                # --- 2) CLICK “AFFICHER PLUS DE RÉSULTATS” ---

                try:
                    show_more_button = driver.find_element(
                        By.CSS_SELECTOR,
                        "button.a83ed08757.c21c56c305.bf0537ecb5.f671049264.af7297d90d.c0e0affd09"
                    )
                    driver.execute_script("arguments[0].scrollIntoView(true);", show_more_button)
                    time.sleep(1)
                    show_more_button.click()
                    print("Clicked 'Afficher plus de résultats'. Waiting for load...")
                    time.sleep(5)
                except (NoSuchElementException, ElementClickInterceptedException):
                    print("No 'Afficher plus de résultats' button found or couldn't click. End of results.")
                    break

            # --- 3) SCRAPE CURRENTLY LOADED HOTELS ---
            # We do this each iteration, but we only add newly discovered ones to all_hotels_data
            hotel_cards = driver.find_elements(By.CSS_SELECTOR, "div[data-testid='property-card']")
            print(f"Total hotels now visible: {len(hotel_cards)}")

            # Extract data for each card
            for card in hotel_cards[prev_total_hotels_count:]:  # process only new ones
                hotel_info = {}

                # 1. Name
                try:
                    name_div = card.find_element(By.CSS_SELECTOR, "div[data-testid='title']")
                    hotel_info["Name"] = name_div.text.strip()
                except:
                    hotel_info["Name"] = "N/A"

                # 2. Address
                try:
                    address_span = card.find_element(By.CSS_SELECTOR, "span[data-testid='address']")
                    hotel_info["Address"] = address_span.text.strip()
                except:
                    hotel_info["Address"] = "N/A"

                # 3. Description
                try:
                    desc_div = card.find_element(By.CSS_SELECTOR, "div.abf093bdfe")
                    hotel_info["Description"] = desc_div.text.strip()
                except:
                    hotel_info["Description"] = "N/A"

                # 4. Rating & Reviews
                try:
                    score_div = card.find_element(By.CSS_SELECTOR, "div[data-testid='review-score']")
                    numeric_score = score_div.find_element(By.CLASS_NAME, "ac4a7896c7").text.strip()
                    hotel_info["Rating"] = numeric_score
                    text_rating_elem = score_div.find_element(By.CLASS_NAME, "a3b8729ab1.e6208ee469.cb2cbb3ccb")
                    hotel_info["RatingText"] = text_rating_elem.text.strip()
                    reviews_elem = score_div.find_element(By.CSS_SELECTOR, "div.abf093bdfe.f45d8e4c32.d935416c47")
                    hotel_info["NumReviews"] = reviews_elem.text.strip()
                except:
                    hotel_info["Rating"] = "N/A"
                    hotel_info["RatingText"] = "N/A"
                    hotel_info["NumReviews"] = "N/A"

                # 5. Hotel Link
                try:
                    title_link = card.find_element(By.CSS_SELECTOR, "a[data-testid='title-link']")
                    hotel_info["HotelLink"] = title_link.get_attribute("href")
                except:
                    hotel_info["HotelLink"] = "N/A"

                all_hotels_data.append(hotel_info)

            prev_total_hotels_count = len(hotel_cards)

        print(f"Final total hotels collected: {len(all_hotels_data)}")

        # 4) SAVE TO CSV
        csv_filename = "sustainable_hotels_paris3.csv"
        fieldnames = ["Name", "Address", "Description", "Rating", "RatingText", "NumReviews", "HotelLink"]
        with open(csv_filename, "w", newline="", encoding="utf-8") as f:
            writer = csv.DictWriter(f, fieldnames=fieldnames)
            writer.writeheader()
            writer.writerows(all_hotels_data)

        print(f"Data saved to '{csv_filename}'.")

    finally:
        driver.quit()

if __name__ == "__main__":
    scrape_sustainable_hotels_in_paris()


No cookie popup found.
Hotel count before scroll: 25, after scroll: 75
Total hotels now visible: 75
Hotel count before scroll: 75, after scroll: 75
No new hotels loaded by scrolling. Let's try the 'Afficher plus de résultats' button.
Clicked 'Afficher plus de résultats'. Waiting for load...
Total hotels now visible: 100
Hotel count before scroll: 100, after scroll: 100
No new hotels loaded by scrolling. Let's try the 'Afficher plus de résultats' button.
Clicked 'Afficher plus de résultats'. Waiting for load...
Total hotels now visible: 125
Hotel count before scroll: 125, after scroll: 125
No new hotels loaded by scrolling. Let's try the 'Afficher plus de résultats' button.
Clicked 'Afficher plus de résultats'. Waiting for load...
Total hotels now visible: 150
Hotel count before scroll: 150, after scroll: 150
No new hotels loaded by scrolling. Let's try the 'Afficher plus de résultats' button.
Clicked 'Afficher plus de résultats'. Waiting for load...
Total hotels now visible: 175
Hotel 

## Collecting Reviews

In [ ]:
import csv
import time
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.common.exceptions import (
    NoSuchElementException,
    ElementClickInterceptedException,
    TimeoutException
)
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager

def scrape_hotel_details(hotel_url):
    """
    Given a single hotel URL, this function:
      1) Loads the page
      2) Extracts the full description text
      3) Clicks the 'Reviews' tab
      4) Scrapes all reviews (across multiple pages, if desired)
      5) Scrapes rating subscores
      6) Returns a dictionary with 'full_description', 'all_reviews_text', 'rating_subscores', etc.
    """
    hotel_data = {
        "url": hotel_url,
        "full_description": "",
        "all_reviews_text": "",
        "rating_subscores": {},  # e.g., {"Personnel": 8.7, "Propreté": 8.5, ...}
    }

    driver = webdriver.Chrome()
    wait = WebDriverWait(driver, 15)
    try:
        driver.get(hotel_url)
        time.sleep(10)  # Let page load (consider explicit waits in production)
        try:
            cookie_btn = wait.until(EC.element_to_be_clickable(
                (By.CSS_SELECTOR, "button#onetrust-reject-all-handler")
            ))
            cookie_btn.click()
            print("Rejected cookies.")
        except:
            print("No cookie popup found.")

        # 1) Extract the Full Description
        try:
            desc_elem = driver.find_element(By.CSS_SELECTOR, "p[data-testid='property-description']")
            hotel_data["full_description"] = desc_elem.text.strip()
        except NoSuchElementException:
            # Fallback if data-testid not found
            try:
                desc_elem = driver.find_element(By.CSS_SELECTOR, "div.hp_desc_main_content")
                hotel_data["full_description"] = desc_elem.text.strip()
            except NoSuchElementException:
                print("No full description found.")
        print(hotel_data["full_description"])
        # 2) Locate & Click the 'Reviews' tab
        try:
            reviews_tab_button = wait.until(
                EC.element_to_be_clickable(
                    (By.CSS_SELECTOR, "a#reviews-tab-trigger[data-testid*='Tab-Trigger-reviews']")
                )
            )
            reviews_tab_button.click()
            time.sleep(3)
        except (NoSuchElementException, TimeoutException):
            print("No reviews tab found.")
        # 3) Scrape multiple pages of reviews
        all_reviews = []
        page_counter = 0
        max_review_pages = 35  # or as many as you want

        while page_counter < max_review_pages:
            page_counter +=1
            try:
                wait.until(EC.presence_of_element_located((By.CSS_SELECTOR, "div[data-testid='review-cards']")))
            except TimeoutException:
                print("Review container not found.")
                break
            
            review_cards = driver.find_elements(By.CSS_SELECTOR, "div[data-testid='review-card']")
            for rc in review_cards:
                positive, negative = "", ""
                # Extract positive
                try:
                    pos_container = rc.find_element(By.XPATH, "//div[@data-testid='review-positive-text']//div[@class='a53cbfa6de b5726afd0b']/span")
                    positive = pos_container.text.strip()
                    print("positive : ",positive)
                except NoSuchElementException:
                    pass
                # Extract negative
                try:
                    neg_container = rc.find_element(By.XPATH, "//div[@data-testid='review-negative-text']//div[@class='a53cbfa6de b5726afd0b']/span")
                    negative = neg_container.text.strip()
                    print("negative : ",negative)
                except NoSuchElementException:
                    pass

                combined_text = ""
                if positive:
                    combined_text += f"(+) {positive}\n"
                if negative:
                    combined_text += f"(-) {negative}\n"

                if combined_text:
                    print(combined_text)
                    all_reviews.append(combined_text)
            # Try to find "Next Page" button
            try:
                next_button = driver.find_element(
                    By.CSS_SELECTOR,
                    "button[aria-label*='Page suivante'], button[aria-label*='Next page']"
                )
                # If the button is disabled, we've reached the end
                if not next_button.is_enabled():
                    print("Next page button is disabled. No more reviews to load.")
                    break

                # Otherwise, click next and continue
                driver.execute_script("arguments[0].scrollIntoView(true);", next_button)
                time.sleep(1)
                next_button.click()
                time.sleep(3)
            except NoSuchElementException:
                print("No 'Next page' button found, likely the last page of reviews.")
                break
        print("joining reviews")
        hotel_data["all_reviews_text"] = "\n".join(all_reviews)
        print("scraping subscore")
        try:
            # Locate and click the close button by ID
            close_button = driver.find_element(By.ID, "reviews_sheet_close_button")
            close_button.click()
            print("Close button clicked successfully.")
        except NoSuchElementException:
            print("Close button not found.")
        # 4) Scrape rating subscores (Personnel, Propreté, etc.)
        try:
            # Find all subscore elements
            subscore_elems = driver.find_elements(By.XPATH, "//div[contains(@class, 'b817090550') and contains(@class, 'a7cf1a6b1d')]//div[@data-testid='review-subscore']")
            print("Number of subscore elements found:", len(subscore_elems))

            # Loop through each subscore element
            for elem in subscore_elems:
                try:
                    # Extract label (e.g., "Personnel")
                    label_span = elem.find_element(By.CSS_SELECTOR, "div[class*='ccb65902b2'] span")
                    label = label_span.text.strip()

                    # Extract score (e.g., "8,7")
                    score_div = elem.find_element(By.CSS_SELECTOR, "div[class*='bdc1ea4a28']")
                    score_str = score_div.text.strip()

                    # Convert score to float
                    numeric_val = float(score_str.replace(',', '.'))
                    print("num",numeric_val)
                    # Store the result in hotel_data
                    hotel_data["rating_subscores"][label] = numeric_val

                except NoSuchElementException as e:
                    # Log which element failed
                    print(f"Failed to process subscore element: {e}")
                    continue  # Continue processing other elements
        except NoSuchElementException:
            print("No subscore elements found.")
    except Exception as e:
        print(f"Error scraping {hotel_url}: {e}")
    finally:
        driver.quit()

    return hotel_data

def main():
    csv_input_file = "sustainable_hotels_paris3.csv"  # The CSV where you have your hotel links
    csv_output_file = "hotel_details.csv"

    # Read the CSV of scraped hotels
    hotel_links = []
    with open(csv_input_file, "r", encoding="utf-8") as f:
        reader = csv.DictReader(f)
        for row in reader:
            link = row.get("HotelLink", "").strip()
            if link and link != "N/A":
                hotel_links.append(link)

    print(f"Found {len(hotel_links)} hotel links in '{csv_input_file}'.")

    # Scrape each hotel
    all_hotel_details = []
    for url in hotel_links:
        details = scrape_hotel_details(url)
        all_hotel_details.append(details)

    # Optionally, write results to new CSV
    fieldnames = ["url", "full_description", "all_reviews_text", "rating_subscores"]
    with open(csv_output_file, "w", newline="", encoding="utf-8") as f:
        writer = csv.DictWriter(f, fieldnames=fieldnames)
        writer.writeheader()
        for hd in all_hotel_details:
            row = {
                "url": hd["url"],
                "full_description": hd["full_description"],
                "all_reviews_text": hd["all_reviews_text"],
                # Convert dict to string or JSON:
                "rating_subscores": str(hd["rating_subscores"])
            }
            writer.writerow(row)

    print(f"Scraped details saved to '{csv_output_file}'.")

if __name__ == "__main__":
    main()

Found 208 hotel links in 'sustainable_hotels_paris3.csv'.
Rejected cookies.
Le NH Paris Gare de l'Est est situé en face de la gare de l’Est et de la station de métro du même nom, ce qui vous permettra de rejoindre directement des sites d’intérêt tels que Saint-Michel et le Quartier latin. L’hôtel dispose d’un bar dans le hall avec des fenêtres en verre au plomb.

Les chambres présentent une décoration contemporaine. Les chambres sont équipées d’une télévision par satellite à écran LCD et d’une machine à café.

Un buffet de style américain est servi tous les matins dans la salle prévue à cet effet ou en chambre. L’établissement dispose d’une réception ouverte 24h/24. Vous pourrez profiter d’une connexion Wi-Fi gratuite dans tout l’établissement, ainsi que d’une connexion par câble dans votre chambre.

La gare du Nord toute proche se trouve à seulement 5 minutes à pied de l’hôtel. Vous rejoindrez le musée des Arts et Métiers en 20 minutes à pied.
positive :  L amabilité du personnel, pro

## Collecting Loc & Lat using OpenTripMap API

In [ ]:
import csv
import requests
import time

OTM_API_KEY = "5ae2e3f221c38a28845f05b67cdfbc05f7cca9a34980fed59617ec85"

def geocode_address(address: str) -> tuple:
    """
    Calls the OpenTripMap API to geocode the address (string).
    Returns (latitude, longitude) as floats or (None, None) if not found.
    """
    # Base endpoint for geocoding with OTM
    base_url = "https://api.opentripmap.com/0.1/en/places/geoname"
    
    # Prepare params
    params = {
        "name": address,
        "apikey": OTM_API_KEY,
    }
    
    try:
        r = requests.get(base_url, params=params, timeout=10)
        if r.status_code == 200:
            data = r.json()
            # The OTM /geoname endpoint typically returns fields like 'lat' and 'lon'
            # Example response:
            #   {
            #       "name": "Paris",
            #       "lat": 48.85341,
            #       "lon": 2.3488,
            #       "country": "FR",
            #       ...
            #   }
            lat = data.get("lat")
            lon = data.get("lon")
            if lat is not None and lon is not None:
                return float(lat), float(lon)
        else:
            print(f"Error geocoding '{address}': HTTP {r.status_code}")
    except Exception as e:
        print(f"Exception geocoding '{address}': {e}")
    
    return (None, None)

def main():
    input_csv = "sustainable_hotels_paris3.csv"
    output_csv = "sustainable_hotels_paris_with_coords.csv"

    # Read the CSV of hotels
    rows = []
    with open(input_csv, "r", encoding="utf-8") as f:
        reader = csv.DictReader(f)
        fieldnames = reader.fieldnames
        
        # We'll add two new columns: "Latitude" and "Longitude"
        if "Latitude" not in fieldnames:
            fieldnames.append("Latitude")
        if "Longitude" not in fieldnames:
            fieldnames.append("Longitude")
        
        # Collect row data
        for row in reader:
            rows.append(row)

    print(f"Read {len(rows)} rows from '{input_csv}'.")

    # For each row, get the address, call geocode, store lat/long
    for idx, row in enumerate(rows, start=1):
        address = row.get("Address", "").strip()  # Adjust the column name if needed
        if not address:
            print(f"Row {idx}: No address, skipping geocoding.")
            continue
        
        print(f"Row {idx}: Geocoding address: {address}")
        lat, lon = geocode_address(address)
        row["Latitude"] = lat if lat is not None else ""
        row["Longitude"] = lon if lon is not None else ""
        
        # Sleep briefly to avoid overwhelming the API
        time.sleep(1)

    # Write out new CSV
    with open(output_csv, "w", newline="", encoding="utf-8") as f:
        writer = csv.DictWriter(f, fieldnames=fieldnames)
        writer.writeheader()
        for row in rows:
            writer.writerow(row)

    print(f"Enriched CSV with lat/lon saved to '{output_csv}'.")

if __name__ == "__main__":
    main()